#Решение практической части. Эксперимент с ALS, подбор оптимальных параметров iterations, regularization, factors

In [ ]:
!pip install cython

In [1]:
!pip install implicit

     |████████████████████████████████| 1.1 MB 8.4 MB/s 
  Created wheel for implicit: filename=implicit-0.4.4-cp37-cp37m-linux_x86_64.whl size=3406617 sha256=e6af6de026b9775860b335ead5acb805b801cf538e6f9d718c4c29ba8e96463c
  Stored in directory: /root/.cache/pip/wheels/44/7e/7d/a17324ea207cfbe76aca878b5b8ca0aa932cf55d163329be37
Successfully built implicit


In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

# Для работы с матрицами
from scipy.sparse import csr_matrix

# Матричная факторизация
from implicit.als import AlternatingLeastSquares
from implicit.nearest_neighbours import bm25_weight, tfidf_weight

# Функции из 1-ого вебинара
import os, sys

module_path = os.path.abspath(os.path.join(os.pardir))
if module_path not in sys.path:
    sys.path.append(module_path)
    

In [3]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
data = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/data/transaction_data.csv')

data.columns = [col.lower() for col in data.columns]
data.rename(columns={'household_key': 'user_id',
                    'product_id': 'item_id'},
           inplace=True)


test_size_weeks = 3

data_train = data[data['week_no'] < data['week_no'].max() - test_size_weeks]
data_test = data[data['week_no'] >= data['week_no'].max() - test_size_weeks]

data_train.head(10)

user_id    basket_id  day  ...  week_no  coupon_disc  coupon_match_disc
0     2375  26984851472    1  ...        1          0.0                0.0
1     2375  26984851472    1  ...        1          0.0                0.0
2     2375  26984851472    1  ...        1          0.0                0.0
3     2375  26984851472    1  ...        1          0.0                0.0
4     2375  26984851472    1  ...        1          0.0                0.0
5     2375  26984851516    1  ...        1          0.0                0.0
6     2375  26984851516    1  ...        1          0.0                0.0
7     2375  26984851516    1  ...        1          0.0                0.0
8     2375  26984851516    1  ...        1          0.0                0.0
9     2375  26984851516    1  ...        1          0.0                0.0

[10 rows x 12 columns]

In [5]:
item_features = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/data/product.csv')
item_features.columns = [col.lower() for col in item_features.columns]
item_features.rename(columns={'product_id': 'item_id'}, inplace=True)

item_features.head(2)

item_id  manufacturer  ...           sub_commodity_desc curr_size_of_product
0    25671             2  ...          ICE - CRUSHED/CUBED                22 LB
1    26081             2  ...  NO SUBCOMMODITY DESCRIPTION                     

[2 rows x 7 columns]

In [6]:
item_features.department.unique()

array(['GROCERY', 'MISC. TRANS.', 'PASTRY', 'DRUG GM', 'MEAT-PCKGD',
       'SEAFOOD-PCKGD', 'PRODUCE', 'NUTRITION', 'DELI', 'COSMETICS',
       'MEAT', 'FLORAL', 'TRAVEL & LEISUR', 'SEAFOOD', 'MISC SALES TRAN',
       'SALAD BAR', 'KIOSK-GAS', 'ELECT &PLUMBING', 'GRO BAKERY',
       'GM MERCH EXP', 'FROZEN GROCERY', 'COUP/STR & MFG', 'SPIRITS',
       'GARDEN CENTER', 'TOYS', 'CHARITABLE CONT', 'RESTAURANT', 'RX',
       'PROD-WHS SALES', 'MEAT-WHSE', 'DAIRY DELI', 'CHEF SHOPPE', 'HBC',
       'DELI/SNACK BAR', 'PORK', 'AUTOMOTIVE', 'VIDEO RENTAL', ' ',
       'CNTRL/STORE SUP', 'HOUSEWARES', 'POSTAL CENTER', 'PHOTO', 'VIDEO',
       'PHARMACY SUPPLY'], dtype=object)

In [7]:
result = data_test.groupby('user_id')['item_id'].unique().reset_index()
result.columns=['user_id', 'actual']
result.head(2)

user_id                                             actual
0        1  [879517, 934369, 1115576, 1124029, 5572301, 65...
1        3  [823704, 834117, 840244, 913785, 917816, 93870...

In [8]:
popularity = data_train.groupby('item_id')['quantity'].sum().reset_index()
popularity.rename(columns={'quantity': 'n_sold'}, inplace=True)

top_5000 = popularity.sort_values('n_sold', ascending=False).head(5000).item_id.tolist()

In [9]:
data_train.head(5)

user_id    basket_id  day  ...  week_no  coupon_disc  coupon_match_disc
0     2375  26984851472    1  ...        1          0.0                0.0
1     2375  26984851472    1  ...        1          0.0                0.0
2     2375  26984851472    1  ...        1          0.0                0.0
3     2375  26984851472    1  ...        1          0.0                0.0
4     2375  26984851472    1  ...        1          0.0                0.0

[5 rows x 12 columns]

In [10]:
# Заведем фиктивный item_id

data_train.loc[~data_train['item_id'].isin(top_5000), 'item_id'] = 999_999

user_item_matrix = pd.pivot_table(data_train, 
                                  index='user_id', columns='item_id', 
                                  values='quantity', # Можно пробовать другие варианты
                                  aggfunc='count', 
                                  fill_value=0
                                 )

user_item_matrix = user_item_matrix.astype(float) # необходимый тип матрицы для implicit

# переведем в формат saprse matrix
sparse_user_item = csr_matrix(user_item_matrix)

user_item_matrix.head(3)

/usr/local/lib/python3.7/dist-packages/pandas/core/indexing.py:1763: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(loc, value)


item_id  202291    397896    420647    ...  15927850  16809471  17105257
user_id                                ...                              
1             0.0       0.0       0.0  ...       0.0       0.0       0.0
2             0.0       0.0       0.0  ...       0.0       0.0       0.0
3             0.0       0.0       0.0  ...       0.0       0.0       0.0

[3 rows x 5001 columns]

In [11]:
userids = user_item_matrix.index.values
itemids = user_item_matrix.columns.values

matrix_userids = np.arange(len(userids))
matrix_itemids = np.arange(len(itemids))

id_to_itemid = dict(zip(matrix_itemids, itemids))
id_to_userid = dict(zip(matrix_userids, userids))

itemid_to_id = dict(zip(itemids, matrix_itemids))
userid_to_id = dict(zip(userids, matrix_userids))

# ALS

In [12]:
def precision_at_k(recommended_list, bought_list, k=5):
    bought_list = np.array(bought_list)
    recommended_list = np.array(recommended_list)
    bought_list = bought_list  # Тут нет [:k] !!
    recommended_list = recommended_list[:k]
    flags = np.isin(bought_list, recommended_list)
    #print(flags)
    precision = flags.sum() / len(recommended_list)
    return precision

In [13]:
def get_recommendations(user, model, N=5):
    res = [id_to_itemid[rec[0]] for rec in 
                    model.recommend(userid=userid_to_id[user], 
                                    user_items=sparse_user_item,   # на вход user-item matrix
                                    N=N, 
                                    filter_already_liked_items=False, 
                                    filter_items=None, 
                                    recalculate_user=True)]
    return res

In [22]:
factors = np.arange(16, 224, 8)

In [23]:
factors

array([ 16,  24,  32,  40,  48,  56,  64,  72,  80,  88,  96, 104, 112,
       120, 128, 136, 144, 152, 160, 168, 176, 184, 192, 200, 208, 216])

In [ ]:
iterations = np.arange(15, 85, 5)

In [ ]:
iterations

array([15, 20, 25, 30, 35, 40, 45, 50, 55, 60, 65, 70, 75, 80])

In [ ]:
for num_factors in factors: 
  for num_iterations in iterations: 
    model = AlternatingLeastSquares(factors=num_factors, 
                                regularization=0.05,
                                iterations=num_iterations, 
                                calculate_training_loss=True, 
                                num_threads=10,
                                use_gpu=True)  #поменять в колабе на True [!!!]

    model.fit(csr_matrix(user_item_matrix).T.tocsr(),  # На вход item-user matrix
          show_progress=True)
    
    recs = model.recommend(userid=userid_to_id[2],  # userid - id от 0 до N
                        user_items=csr_matrix(user_item_matrix).tocsr(),   # на вход user-item matrix
                        N=5, # кол-во рекомендаций 
                        filter_already_liked_items=False, 
                        filter_items=None, 
                        recalculate_user=True)
    
    result[f'num_factors={num_factors}_iter={num_iterations}'] = \
                        result['user_id'].apply(lambda x: get_recommendations(x, model=model, N=5))

GPU training requires factor size to be a multiple of 32. Increasing factors from 16 to 32.


In [ ]:
result

user_id  ...                       num_factors=216_iter=80
0           1  ...     [962568, 986912, 1105488, 878996, 965766]
1           3  ...    [908531, 1098066, 1022003, 914190, 866140]
2           5  ...   [999999, 1082185, 1126899, 916122, 1058997]
3           6  ...   [5568378, 10149640, 847789, 874972, 878996]
4           7  ...     [1133018, 995242, 995785, 860776, 893018]
...       ...  ...                                           ...
1986     2494  ...     [860776, 961554, 6034857, 904360, 999999]
1987     2497  ...    [1110843, 854852, 979707, 823704, 5585510]
1988     2498  ...   [840361, 862349, 1053690, 1070820, 5568378]
1989     2499  ...    [929668, 862349, 901062, 1044078, 1053690]
1990     2500  ...  [1096036, 1098066, 5569230, 911812, 1029743]

[1991 rows x 366 columns]

In [ ]:
%%time
    
result.apply(lambda row: precision_at_k(row[f'num_factors={num_factors}_iter={num_iterations}'], \
                                                            row['actual']), axis=1).mean()


CPU times: user 150 ms, sys: 5.08 ms, total: 155 ms
Wall time: 144 ms


0.12074334505273653

In [ ]:
df_res = pd.DataFrame(columns=['parameters', 'presision_at_k'])
i = 0
for column in result.columns[2:]:
    a = round(result.apply(lambda row: precision_at_k(row[column], row['actual']), axis=1).mean(), 3)
    #print(column, a)
    #df = pd.DataFrame([column, a])
    df_res.loc[i] = [column, a]
    i += 1

In [ ]:
df_res.sort_values(by='presision_at_k', ascending=False).head(10)

parameters  presision_at_k
14  num_factors=24_iter=15           0.165
1   num_factors=16_iter=20           0.165
15  num_factors=24_iter=20           0.164
20  num_factors=24_iter=45           0.163
19  num_factors=24_iter=40           0.163
5   num_factors=16_iter=40           0.163
7   num_factors=16_iter=50           0.163
8   num_factors=16_iter=55           0.163
22  num_factors=24_iter=55           0.163
29  num_factors=32_iter=20           0.163

In [ ]:
#результаты вышли очеь посредственные. Скорее всего итерации не так сильно влияют на точность наших рекомендаций. 
#попробуем разобраться с параметром регуляризация и ее сочетанием с кол-вом факторов. 

In [24]:
factors_2 = np.arange(16, 224, 16)

In [25]:
factors_2 

array([ 16,  32,  48,  64,  80,  96, 112, 128, 144, 160, 176, 192, 208])

In [16]:
regularizations = np.arange(0.0001, 0.01, 0.0005)

In [17]:
regularizations

array([0.0001, 0.0006, 0.0011, 0.0016, 0.0021, 0.0026, 0.0031, 0.0036,
       0.0041, 0.0046, 0.0051, 0.0056, 0.0061, 0.0066, 0.0071, 0.0076,
       0.0081, 0.0086, 0.0091, 0.0096])

In [26]:
for num_factors in factors_2: 
  for num_regs in regularizations: 
    model = AlternatingLeastSquares(factors=num_factors, 
                                regularization=num_regs,
                                iterations=15, 
                                calculate_training_loss=True, 
                                num_threads=10,
                                use_gpu=True)  #поменять в колабе на True [!!!]

    model.fit(csr_matrix(user_item_matrix).T.tocsr(),  # На вход item-user matrix
          show_progress=True)
    
    recs = model.recommend(userid=userid_to_id[2],  # userid - id от 0 до N
                        user_items=csr_matrix(user_item_matrix).tocsr(),   # на вход user-item matrix
                        N=5, # кол-во рекомендаций 
                        filter_already_liked_items=False, 
                        filter_items=None, 
                        recalculate_user=True)
    
    result[f'num_factors={num_factors}_reg={num_regs}'] = \
                        result['user_id'].apply(lambda x: get_recommendations(x, model=model, N=5))

In [27]:
result.head(2)

user_id  ...                   num_factors=208_reg=0.0096
0        1  ...   [986912, 962568, 1033142, 5569374, 995242]
1        3  ...  [914190, 1098066, 908531, 1022003, 1101010]

[2 rows x 262 columns]

In [28]:
%%time
    
result.apply(lambda row: precision_at_k(row[f'num_factors={num_factors}_reg={num_regs}'], \
                                                            row['actual']), axis=1).mean()

CPU times: user 201 ms, sys: 20.7 ms, total: 222 ms
Wall time: 194 ms


0.12516323455549874

In [32]:
df_res_2 = pd.DataFrame(columns=['parameters', 'presision_at_k'])
i = 0
for column in result.columns[2:]:
    a = round(result.apply(lambda row: precision_at_k(row[column], row['actual']), axis=1).mean(), 3)
    #print(column, a)
    #df = pd.DataFrame([column, a])
    df_res_2.loc[i] = [column, a]
    i += 1

In [33]:
df_res_2.sort_values(by='presision_at_k', ascending=False).head(10)

parameters  presision_at_k
11                num_factors=16_reg=0.0056           0.165
32                num_factors=32_reg=0.0061           0.164
29  num_factors=32_reg=0.004600000000000001           0.164
19                num_factors=16_reg=0.0096           0.163
17                num_factors=16_reg=0.0086           0.163
16                num_factors=16_reg=0.0081           0.163
34                num_factors=32_reg=0.0071           0.163
27                num_factors=32_reg=0.0036           0.163
35                num_factors=32_reg=0.0076           0.163
7                 num_factors=16_reg=0.0036           0.163

In [34]:
# Результаты те же, что и с итерациями. 
# Может быть попробовать со взвешиванием bm_25? 

# ДЗ

1) Попытаться ответить на вопросы/выдвинуть гипотезы

2) Доделать прошлые домашния задания

3) Прочитать статьи BM25/MatrixFactorization

## Практика:

4) Поэкспериментировать с ALS (grid-search)

# Links

BM25

https://en.wikipedia.org/wiki/Okapi_BM25#:~:text=BM25%20is%20a%20bag%2Dof,slightly%20different%20components%20and%20parameters.


Matrix factorization (ALS, SVD)
https://datasciencemadesimpler.wordpress.com/tag/alternating-least-squares/

## Ответы на теорию: 

https://ru.wikipedia.org/wiki/Okapi_BM25
Как это работает расписано в статье на хабре: 
https://habr.com/ru/post/162937/
Там же есть ссылка на документ с расчетом bm25. 


1) BM-25 прочел, добавил статью на Хабр про эту метрику. 

2) В начале нашего эксперимента мы говорим про рекомендательную систему, про рассылки пользователя, про технологии и методы, которые мы будем применять. Но мы не говорим о сегментировании наших пользователей. 

А ведь это очень важно. Нужно сделать шаг назад и попробовать составить модель оттока, она подскажет кто уже от нас ушел. После этого мы можем попробовать классифицировать оставшихся на: 
- лояльных. Они и так у нас купят
- лояльных, но с ними нужно коммуницировать. Вопрос: как? Вот тут и нужна рекомендашка
- нелояльных, которые не станут лояльными после коммуникации. 

В общем, просто составить рекомендательную систему - не получится. Тут нужен комплексный подход. Дальше больше - делаем uplift по сегментациям, фиксируем через модель оттока кто от нас уйдет. Если получится, выясняем почему от нас ушли и вводим наилучшие практики в наш бизнес. 
